In [1]:
import os
import sys
import math
import numpy as np
# import pandas as pd
import scipy.io as sio
from sklearn import preprocessing
from scipy.signal import butter, lfilter
from scipy.io import loadmat

In [3]:
# 这个函数负责从mat文件中加载数据,并对每个trial中的数据进行带通滤波
# 得到delta/theta/alpha/beta/gamma 5个频带上的特征
# 输入:
#   file: mat文件路径 
#   name: 被试的姓名缩写
#   idx: 被试的第几次数据 0/1/2 
# 输出:
#   decomposed_de: 每个trail经过带通滤波分解后的特征,shape为 (trial, channel, band)
#   label: 每个trial对应的标签
def decompose(file, name, idx):
    # trial*channel*sample
    data = loadmat(file)
    frequency = 200

    # 存储最终的特征数据
    decomposed_de = np.empty([0, 62, 5])
    label = np.array([])
    all_label = []
    # 根据idx选择不同的trial标签    
    if idx == 0:
        all_label = [1,2,3,0,2,0,0,1,0,1,2,1,1,1,2,3,2,2,3,3,0,3,0,3]
    elif idx == 1:
        all_label = [2,1,3,0,0,2,0,2,3,3,2,3,2,0,1,1,2,1,0,3,0,1,3,1]
    else:
        all_label = [1,2,2,1,3,3,3,1,1,2,1,0,2,3,3,0,2,3,0,0,2,0,1,0]

    # 24代表了24个影片
    for trial in range(24):
        # 加载trial的数据
        # tmp_idx = trial + 3
        # tmp_name = list(data.keys())[tmp_idx]
        tmp_trial_signal = data[name + '_eeg' + str(trial + 1)]
        num_sample = int(len(tmp_trial_signal[0]) / 100)
        print('{}-{}'.format(trial + 1, num_sample))

        # 存储该trial的特征
        temp_de = np.empty([0, num_sample])
        # 存储该trial的标签
        label = np.append(label, [all_label[trial]] * num_sample)

        for channel in range(62):
            trial_signal = tmp_trial_signal[channel]
            # 因为SEED数据没有基线信号部分
            # order 是滤波器的阶数
            # 对原始信号进行带通滤波,得到5个频带
            delta = butter_bandpass_filter(trial_signal, 1, 4, frequency, order=3)
#             print(len(delta))
#             print(delta)
            theta = butter_bandpass_filter(trial_signal, 4, 8, frequency, order=3)
            alpha = butter_bandpass_filter(trial_signal, 8, 14, frequency, order=3)
            beta = butter_bandpass_filter(trial_signal, 14, 31, frequency, order=3)
            gamma = butter_bandpass_filter(trial_signal, 31, 51, frequency, order=3)

            # 计算每个频带每个采样点的DE特征
            DE_delta = np.zeros(shape=[0], dtype=float)
            DE_theta = np.zeros(shape=[0], dtype=float)
            DE_alpha = np.zeros(shape=[0], dtype=float)
            DE_beta = np.zeros(shape=[0], dtype=float)
            DE_gamma = np.zeros(shape=[0], dtype=float)

            for index in range(num_sample):
                DE_delta = np.append(DE_delta, compute_DE(delta[index * 100:(index + 1) * 100]))
                DE_theta = np.append(DE_theta, compute_DE(theta[index * 100:(index + 1) * 100]))
                DE_alpha = np.append(DE_alpha, compute_DE(alpha[index * 100:(index + 1) * 100]))
                DE_beta = np.append(DE_beta, compute_DE(beta[index * 100:(index + 1) * 100]))
                DE_gamma = np.append(DE_gamma, compute_DE(gamma[index * 100:(index + 1) * 100]))
            # 拼接不同频带的特征
            temp_de = np.vstack([temp_de, DE_delta])
            temp_de = np.vstack([temp_de, DE_theta])
            temp_de = np.vstack([temp_de, DE_alpha])
            temp_de = np.vstack([temp_de, DE_beta])
            temp_de = np.vstack([temp_de, DE_gamma])

        # 转换维度为(频带,采样点,通道)
        temp_trial_de = temp_de.reshape(-1, 5, num_sample)
        # (x, y, z) -> (z, x, y) 相当于 (num_sample, -1, 5)
        temp_trial_de = temp_trial_de.transpose([2, 0, 1])
        
        # 拼接所有的trial
        decomposed_de = np.vstack([decomposed_de, temp_trial_de])

    print("trial_DE shape:", decomposed_de.shape)
    return decomposed_de, label

# 定义butterworth带通滤波器  
def butter_bandpass(lowcut, highcut, fs, order=5):
    nyq = 0.5 * fs
    low = lowcut / nyq
    high = highcut / nyq
    b, a = butter(order, [low, high], btype='band')
    return b, a

# 对原始信号进行带通滤波
def butter_bandpass_filter(data, lowcut, highcut, fs, order=5):
    b, a = butter_bandpass(lowcut, highcut, fs, order=order)
    y = lfilter(b, a, data)
    return y

# 计算DE特征
def compute_DE(signal):
    variance = np.var(signal, ddof=1)
    return math.log(2 * math.pi * math.e * variance) / 2


# 究极整合版
import os
import numpy as np

file_path = './SeedData/SEED_IV/'

# people_name = ['dujingcheng_20131027', 'dujingcheng_20131030', 'dujingcheng_20131107',
#                'mahaiwei_20130712', 'mahaiwei_20131016', 'mahaiwei_20131113',
#                'penghuiling_20131027', 'penghuiling_20131030', 'penghuiling_20131106',
#                'zhujiayi_20130709', 'zhujiayi_20131016', 'zhujiayi_20131105',
#                'wuyangwei_20131127', 'wuyangwei_20131201', 'wuyangwei_20131207',
#                'weiwei_20131130', 'weiwei_20131204', 'weiwei_20131211',
#                'jianglin_20140404', 'jianglin_20140413', 'jianglin_20140419',
#                'liuye_20140411', 'liuye_20140418', 'liuye_20140506',
#                'sunxiangyu_20140511', 'sunxiangyu_20140514', 'sunxiangyu_20140521',
#                'xiayulu_20140527', 'xiayulu_20140603', 'xiayulu_20140610',
#                'jingjing_20140603', 'jingjing_20140611', 'jingjing_20140629',
#                'yansheng_20140601', 'yansheng_20140615', 'yansheng_20140627',
#                'wusifan_20140618', 'wusifan_20140625', 'wusifan_20140630',
#                'wangkui_20140620', 'wangkui_20140627', 'wangkui_20140704',
#                'liuqiujun_20140621', 'liuqiujun_20140702', 'liuqiujun_20140705']

people_name = ['1_20160518', '1_20161125', '1_20161126',
               '2_20150915', '2_20150920', '2_20151012',
               '3_20150919', '3_20151018', '3_20151101',
               '4_20151111', '4_20151118', '4_20151123',
               '5_20160406', '5_20160413', '5_20160420',
               '6_20150507', '6_20150511', '6_20150512',
               '7_20150715', '7_20150717', '7_20150721',
               '8_20151103', '8_20151110', '8_20151117',
               '9_20151028', '9_20151119', '9_20151209',
               '10_20151014', '10_20151021', '10_20151023',
               '11_20150916', '11_20150921', '11_20151011',
               '12_20150725', '12_20150804', '12_20150807',
               '13_20151115', '13_20151125', '13_20161130',
               '14_20151205', '14_20151208', '14_20151215',
               '15_20150508', '15_20150514', '15_20150527']


               
               
# for file_name in os.listdir(file_path):
#     if file_name == "label.mat" or file_name == "readme.txt" or file_name == ".ipynb_checkpoints":
#         continue
#     people_name.append(file_name)

short_name = ['cz', 'cz', 'cz', 'ha', 'ha', 'ha', 'hql', 'hql', 'hql',
              'ldy', 'ldy', 'ldy', 'ly', 'ly', 'ly', 'mhw', 'mhw', 'mhw',
              'mz', 'mz', 'mz', 'qyt', 'qyt', 'qyt', 'rx', 'rx', 'rx',
              'tyc', 'tyc', 'tyc', 'whh', 'whh', 'whh', 'wll', 'wll', 'wll',
              'wq', 'wq', 'wq', 'zjd', 'zjd', 'zjd', 'zjy', 'zjy', 'zjy']

# short_name = ['1', '1', '1', '2', '2', '2', '3', '3', '3', '4', '4', '4', '5', '5', '5', '6', '6', '6', 
#               '7', '7', '7', '8', '8', '8', '9', '9', '9', '10', '10', '10', '11', '11', '11', '12', '12', '12', 
#               '13', '13', '13', '14', '14', '14', '15', '15', '15']

X = np.empty([0, 62, 5])
y = np.empty([0, 1])

for i in range(len(people_name)):
    file_name = file_path + people_name[i] + ".mat"
    print('processing {}'.format(people_name[i]))
    print(file_name)
    decomposed_de, label = decompose(file_name, short_name[i], i % 3)
    X = np.vstack([X, decomposed_de])
    y = np.append(y, label)
    print("已完成=======================================================================================")
    print(i)

np.save("./source/DE0.5s/X_1D.npy", X)
np.save("./source/DE0.5s/y.npy", y)




X = np.load('./source/DE0.5s/X_1D.npy')
y = np.load('./source/DE0.5s/y.npy')
# 生成8*9的矩阵形式
X89 = np.zeros((len(y), 8, 9, 5))
X89[:, 0, 2, :] = X[:, 3, :]
X89[:, 0, 3:6, :] = X[:, 0:3, :]
X89[:, 0, 6, :] = X[:, 4, :]
for i in range(5):
    X89[:, i + 1, :, :] = X[:, 5 + i * 9:5 + (i + 1) * 9, :]
X89[:, 6, 1:8, :] = X[:, 50:57, :]
X89[:, 7, 2:7, :] = X[:, 57:62, :]


processing 1_20160518
./SeedData/SEED_IV/1_20160518.mat
1-336
33601
[2.58841165e-04 3.24777072e-03 1.56806635e-02 ... 5.28434106e+00
 3.32776638e+00 1.32903672e+00]
33601
[8.76077789e-04 6.96149043e-03 2.67000555e-02 ... 6.04189092e+00
 4.15919906e+00 2.23564399e+00]
33601
[8.41944888e-04 6.42218728e-03 2.41249100e-02 ... 5.82515703e+00
 3.97213565e+00 2.08305704e+00]
33601
[1.48762560e-03 1.04687055e-02 3.69798255e-02 ... 6.65032437e+00
 5.90706322e+00 5.11534264e+00]
33601
[1.66682333e-03 1.20086857e-02 4.32553590e-02 ... 7.58074470e+00
 6.44647750e+00 5.26942815e+00]
33601
[1.56726903e-03 1.06831817e-02 3.85598425e-02 ... 4.86974876e+00
 3.99404898e+00 3.08639710e+00]
33601
[1.92850890e-03 1.31083595e-02 4.50175821e-02 ... 6.49392092e+00
 5.87564581e+00 5.21356360e+00]
33601
[1.88299836e-03 1.27619061e-02 4.38002643e-02 ... 6.47902859e+00
 5.86249509e+00 5.20332867e+00]
33601
[1.73224472e-03 1.19273420e-02 4.14332954e-02 ... 6.54140474e+00
 5.93425633e+00 5.28539014e+00]
33601
[1.92

19001
[7.08257693e-04 5.02101868e-03 1.78595070e-02 ... 2.57550283e+00
 2.93963153e+00 3.29182451e+00]
19001
[2.77614260e-03 1.90060384e-02 6.57872326e-02 ... 6.94400572e+00
 7.48008123e+00 7.97853577e+00]
19001
[2.86431926e-03 1.95402269e-02 6.73326626e-02 ... 9.14627874e+00
 9.68775748e+00 1.01983382e+01]
19001
[1.23162884e-03 8.22444239e-03 2.75461773e-02 ... 4.89410073e+00
 5.34603557e+00 5.78781470e+00]
19001
[1.87446514e-03 1.26896573e-02 4.32421007e-02 ... 7.03017167e+00
 7.38539505e+00 7.70828602e+00]
19001
[1.89722041e-03 1.27761295e-02 4.32736207e-02 ... 7.01470025e+00
 7.36480916e+00 7.68276573e+00]
19001
[1.27998378e-03 8.51059458e-03 2.83169449e-02 ... 2.01891986e+00
 2.06504857e+00 2.07696529e+00]
19001
[-1.22309561e-03 -8.00428434e-03 -2.63889668e-02 ...  5.20535273e+00
  5.34887162e+00  5.45702172e+00]
19001
[ 0.00112923  0.00719248  0.02315956 ... -0.11232029 -0.0241184
  0.05271484]
19001
[ 0.0016526   0.0112606   0.03889694 ... -0.45966885 -0.0780263
  0.30858135]
19

39801
[0.00231819 0.01551647 0.05257013 ... 1.39105867 0.78007867 0.1812391 ]
39801
[0.0023125  0.01550054 0.05254902 ... 1.3442313  0.73593701 0.13901833]
39801
[0.0023893  0.01586065 0.05333259 ... 1.26466655 0.66415418 0.07650009]
39801
[ 0.00237793  0.01619004  0.05550507 ... -0.74927059 -1.28612093
 -1.79337941]
39801
[ 0.00089314  0.00605071  0.02058921 ...  0.81514182  0.28346234
 -0.22842802]
39801
[2.42912478e-03 1.63220208e-02 5.52677920e-02 ... 3.96671938e+00
 3.52297347e+00 3.08357725e+00]
39801
[3.85417339e-03 2.61973767e-02 8.96841344e-02 ... 4.04164834e+00
 3.52540534e+00 3.01563365e+00]
39801
[0.00228406 0.01533557 0.05209931 ... 1.29502576 0.69158371 0.1005688 ]
39801
[0.0023125  0.01546926 0.05233341 ... 1.26948835 0.66565373 0.07532798]
39801
[ 0.00253437  0.0172823   0.05948319 ...  0.49546185 -0.15654901
 -0.77340058]
39801
[ 0.0026197   0.01756391  0.05950112 ... -0.38161431 -1.07896548
 -1.73551055]
39801
[ 0.00330236  0.02260427  0.07805669 ... -1.64939678 -2.48

17601
[2.30397081e-04 1.96209535e-03 8.14485281e-03 ... 1.56449080e+00
 1.11055631e+00 6.31778832e-01]
17601
[3.27106967e-04 2.66524253e-03 1.08804834e-02 ... 1.58198236e+00
 1.18103502e+00 7.46230866e-01]
17601
[2.81596432e-04 2.62314085e-03 1.18664741e-02 ... 3.66938971e+00
 3.23801119e+00 2.76887536e+00]
17601
[-1.96264180e-04 -7.62889444e-04 -8.51907221e-04 ...  2.95797374e+00
  2.38227026e+00  1.76947963e+00]
17601
[2.61685573e-04 2.51618916e-03 1.13576883e-02 ... 3.87138777e+00
 3.36800560e+00 2.82387750e+00]
17601
[1.76353321e-04 1.79370111e-03 8.39006359e-03 ... 2.10161234e+00
 1.65137087e+00 1.16413554e+00]
17601
[7.50923819e-04 5.65248150e-03 2.12818100e-02 ... 1.68046388e+00
 1.22326602e+00 7.37403571e-01]
17601
[6.31458666e-04 4.76899662e-03 1.80271187e-02 ... 1.72583438e+00
 1.23993734e+00 7.27419483e-01]
17601
[ 4.94927063e-04  3.92021185e-03  1.53127011e-02 ... -7.57051028e-01
 -1.00422714e+00 -1.25841688e+00]
17601
[ 0.00191429  0.01343547  0.04765197 ... -0.34778001 -0

32401
[2.36085898e-03 1.56871422e-02 5.26001438e-02 ... 4.54233960e+00
 4.45155425e+00 4.32921998e+00]
32401
[1.56726903e-03 1.05068284e-02 3.54378027e-02 ... 3.44801597e+00
 3.34879716e+00 3.21492169e+00]
32401
[1.46771474e-03 9.94362581e-03 3.38126149e-02 ... 3.53617697e+00
 3.45465125e+00 3.33717973e+00]
32401
[-6.25769849e-04 -4.14720839e-03 -1.44009505e-02 ...  4.06281961e+00
  4.11147248e+00  4.12591774e+00]
32401
[9.98387350e-04 6.98539537e-03 2.42920428e-02 ... 1.90350753e+00
 2.05018692e+00 2.18326645e+00]
32401
[-1.16620745e-03 -7.42686390e-03 -2.42305848e-02 ... -4.36861301e+00
 -4.18950448e+00 -3.97074419e+00]
32401
[-0.00252583 -0.01715317 -0.05891649 ... -1.50706649 -1.53841944
 -1.55208734]
32401
[-6.62747158e-04 -4.15972738e-03 -1.33687940e-02 ... -2.36791728e+00
 -2.37509506e+00 -2.36961127e+00]
32401
[-9.92698534e-04 -6.59400422e-03 -2.22069975e-02 ... -2.73605185e+00
 -2.76909803e+00 -2.79607524e+00]
32401
[2.35517016e-03 1.57281012e-02 5.29601941e-02 ... 4.41517320e

...

14001
[-2.70218799e-04 -2.02240069e-03 -7.64861530e-03 ... -1.17569357e+00
 -2.21782353e+00 -3.10665214e+00]
14001
[ 2.58841165e-04  1.77721157e-03  5.87698235e-03 ... -4.69297332e+00
 -4.93564392e+00 -5.27908293e+00]
14001
[-4.43727711e-04 -3.56920687e-03 -1.35201878e-02 ... -4.10281510e+00
 -4.30945382e+00 -4.58437254e+00]
14001
[-5.29059963e-04 -3.95605472e-03 -1.45666664e-02 ... -4.54874560e+00
 -4.73584895e+00 -4.94627931e+00]
14001
[ 4.57949753e-04  2.98326013e-03  9.88511617e-03 ... -3.85709644e+00
 -3.93103350e+00 -4.01397799e+00]
14001
[-5.54659639e-04 -3.85707180e-03 -1.35281297e-02 ... -1.66963976e+00
 -1.72686278e+00 -1.78723648e+00]
14001
[-3.32795783e-04 -1.83922688e-03 -5.36970192e-03 ... -1.77437653e+00
 -1.81611062e+00 -1.84012065e+00]
14001
[-3.81150726e-04 -2.15382316e-03 -7.05068300e-03 ... -6.67000559e-01
 -8.77509406e-01 -1.04721191e+00]
14001
[-3.61239868e-04 -2.68686335e-03 -1.19178914e-02 ... -1.74350899e+00
 -2.21707214e+00 -2.61588477e+00]
14001
[-0.00597041 

36601
[ 0.00546411  0.03728162  0.12855504 ... -2.40720671 -2.46920268
 -2.51459275]
36601
[ 0.00250592  0.01700639  0.05808002 ... -1.80586187 -1.91897397
 -2.02694894]
36601
[ 5.03460288e-04  3.08224997e-03  9.48223477e-03 ... -1.88819846e+00
 -1.75495945e+00 -1.60984117e+00]
36601
[ 0.00800985  0.05445072  0.18725044 ... -6.39079321 -6.48472322
 -6.53755166]
36601
[ 2.21010533e-03  1.48269784e-02  5.02724252e-02 ... -8.82827233e+00
 -8.66241729e+00 -8.43512009e+00]
36601
[ 2.41774714e-04  2.79038819e-03  1.33696543e-02 ... -9.43527309e+00
 -9.39987680e+00 -9.30871531e+00]
36601
[  0.01357921   0.09175397   0.31480983 ... -12.01595017 -11.68379062
 -11.27892436]
36601
[  0.01351094   0.09133811   0.31352345 ... -12.02454864 -11.70082844
 -11.30425028]
36601
[ 0.01280268  0.0872074   0.30060022 ... -7.28145347 -6.98861304
 -6.6486528 ]
36601
[ 5.85948132e-04  3.80246221e-03  1.23286596e-02 ... -3.66324775e+00
 -3.53895107e+00 -3.41117833e+00]
36601
[ 5.90783626e-03  4.01255069e-02  1.

31801
[3.91106156e-03 2.64960451e-02 9.08998523e-02 ... 1.41509212e+01
 1.36310705e+01 1.31118717e+01]
31801
[3.95941650e-03 2.66712654e-02 9.10784033e-02 ... 1.39846491e+01
 1.34923665e+01 1.30004333e+01]
31801
[1.31411668e-03 8.79674539e-03 2.99926638e-02 ... 8.09785208e+00
 7.87680395e+00 7.64942990e+00]
31801
[1.28567260e-03 8.38999222e-03 2.77850845e-02 ... 5.56167555e+00
 5.55609216e+00 5.53741111e+00]
31801
[ 5.68881681e-06 -4.53398146e-04 -3.06796729e-03 ...  3.84814360e+00
  4.07097351e+00  4.27268115e+00]
31801
[-9.50032407e-04 -6.77319780e-03 -2.44650571e-02 ...  1.81568235e+00
  2.36452540e+00  2.88649620e+00]
31801
[-8.44789296e-04 -6.14286665e-03 -2.26384228e-02 ...  1.78385071e+00
  2.30516279e+00  2.79974194e+00]
31801
[-2.19588329e-03 -1.46563126e-02 -5.02443940e-02 ... -6.59037780e-01
  9.62560964e-01  2.54083646e+00]
31801
[3.79444081e-03 2.57712785e-02 8.87590747e-02 ... 2.21494413e+01
 2.14235888e+01 2.06876539e+01]
31801
[1.94557535e-03 1.34690321e-02 4.72483695e-

31001
[0.00203944 0.01357542 0.04554436 ... 0.9740825  0.96056696 0.9341445 ]
31001
[1.34540518e-03 8.71938053e-03 2.83170375e-02 ... 2.72307496e+00
 2.86460946e+00 2.98843283e+00]
31001
[2.13615071e-03 1.39543067e-02 4.61859071e-02 ... 6.11154451e+00
 6.31487835e+00 6.46929590e+00]
31001
[3.76884114e-03 2.44679681e-02 7.99689060e-02 ... 9.51133391e+00
 9.55453539e+00 9.52275842e+00]
31001
[-0.00215891 -0.01475473 -0.05083909 ...  1.03026545  1.49680922
  1.95301311]
31001
[-0.00433488 -0.02946622 -0.10057927 ...  2.52484335  2.65289273
  2.77848087]
31001
[-0.00282734 -0.01860896 -0.06196652 ...  1.92409799  1.98283891
  2.03652494]
31001
[-2.15037275e-03 -1.43411477e-02 -4.84035850e-02 ...  2.43296260e+00
  2.34129900e+00  2.23187900e+00]
31001
[4.77860612e-04 3.24380987e-03 1.10998991e-02 ... 1.78920225e+00
 1.83012985e+00 1.86206935e+00]
31001
[2.10486222e-04 1.11844188e-03 2.59797912e-03 ... 1.64850086e+00
 1.73353837e+00 1.80280703e+00]
31001
[-5.97325765e-04 -4.47431258e-03 -1.6

33001
[ 0.00347587  0.02454645  0.08760385 ... -2.15219642 -2.15896543
 -2.13604828]
33001
[ 0.00351284  0.02463576  0.08752344 ... -2.13523305 -2.13758495
 -2.10801775]
33001
[ 0.00285294  0.01989521  0.07071743 ... -1.46086955 -1.18835054
 -0.90609572]
33001
[-3.72617501e-03 -2.45049412e-02 -8.18998447e-02 ... -7.52214728e+00
 -7.43778488e+00 -7.32507732e+00]
33001
[-3.61239868e-04 -2.28864618e-03 -7.60288508e-03 ... -4.80772214e+00
 -4.90637871e+00 -4.94742331e+00]
33001
[ 2.46041327e-03  1.69785133e-02  5.94613895e-02 ... -9.75894132e+00
 -9.65538564e+00 -9.47293362e+00]
33001
[ 2.47179090e-03  1.70615712e-02  5.97948738e-02 ... -9.68010971e+00
 -9.59431398e+00 -9.42950996e+00]
33001
[ 2.53152348e-03  1.79939741e-02  6.47146699e-02 ... -3.93282668e+00
 -3.81958017e+00 -3.67380968e+00]
33001
[ 1.47055915e-03  1.08333570e-02  4.02331280e-02 ... -3.61651402e+00
 -3.59908174e+00 -3.54544743e+00]
33001
[ 7.79367903e-04  5.31684408e-03  1.90099427e-02 ... -6.29871942e+00
 -6.29113541e+00

In [4]:
np.save("./source/DE0.5s/X89.npy", X89)

In [5]:
X89.shape

(305460, 8, 9, 5)

In [6]:
X.shape

(305460, 62, 5)

In [18]:
count = 0
for i in range(len(y)):
    if y[i] == 1.0:
        count += 1
print(count)
print(y.shape)

105300
(305460,)


In [16]:
tt = np.empty([0, 1])
tt.shape

(0, 1)

In [3]:
np.save("./source/DE0.5s/X_1D.npy", X)

In [5]:
np.save("./source/DE0.5s/y.npy", y)

In [6]:
X = np.load('./source/DE0.5s/X_1D.npy')
y = np.load('./source/DE0.5s/y.npy')
# 生成8*9的矩阵形式
X89 = np.zeros((len(y), 8, 9, 5))
X89[:, 0, 2, :] = X[:, 3, :]
X89[:, 0, 3:6, :] = X[:, 0:3, :]
X89[:, 0, 6, :] = X[:, 4, :]
for i in range(5):
    X89[:, i + 1, :, :] = X[:, 5 + i * 9:5 + (i + 1) * 9, :]
X89[:, 6, 1:8, :] = X[:, 50:57, :]
X89[:, 7, 2:7, :] = X[:, 57:62, :]

In [7]:
X89.shape

(303690, 8, 9, 5)

In [8]:
X.shape

(303690, 62, 5)

In [9]:
count = 0
for i in range(len(y)):
    if y[i] == 1.0:
        count += 1
print(count)
print(y.shape)

82470
(303690,)
